In [42]:
#Importing necessary packages
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.mlab as mlab
import lightgbm as lgb
import seaborn as sns
from sklearn.preprocessing import OneHotEncoder
from sklearn.model_selection import train_test_split
from matplotlib import style
from datetime import datetime, timedelta
import itertools

style.use('ggplot')

In [43]:
#Importing data and setting saving directory

path = "/home/marius/Documents/MT Data/Extensive_incident_list_full.csv"
save_path = "/home/marius/Documents/MTD_Plots/Full data plots"

data = pd.read_csv(path, encoding = "ISO-8859-1")

/home/marius/.local/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3044: DtypeWarning: Columns (5,8,9,13,16,17,19,23,24,25,27,28,29,30,31,32,33,34,38,39,41,42,45,49,50,51,52,53,54,57,58,59,60,61,63,65,66,68,69,70,71,74,77,79,80,86,88,90,91,92,94,96,97,105,126,127,128,129,130,131,132,138,140) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [44]:
len(list(data))

141

## Cleaning data

In [45]:
#Removing columns unneccesarry for regression task
unneccessary_1 = list(data)[:10]
unneccessary_2 = list(data)[11:13]
unneccessary_3 = list(data)[14:16]
unneccessary_4 = [list(data)[17]]
unneccessary_5 = list(data)[22:32]
unneccessary_6 = list(data)[-30:-8]

unneccessary = list(itertools.chain(unneccessary_1, unneccessary_2, unneccessary_3, unneccessary_4, unneccessary_5, unneccessary_6))
data = data.drop(unneccessary, axis=1)

In [ ]:
#

In [48]:
#Unneccessary until I can speak to Kaipeng about the columns
remove_list = ['sys_mod_count',
 'u_unit',
 'sys_class_name',
 'sys_tags',
 'u_supplier',
 'subcategory',
 'correlation_id',
 'u_sap_data',
 'u_sap_component',
 'u_resolved_by',
 'u_resolved_at',
 'calendar_stc',
 'u_reopened_counter',
 'reassignment_count',
 'u_reason_for_waiting',
 'u_qualified_by_it',
 'u_project_related',
 'problem_id',
 'parent',
 'order',
 'opened_by',
 'opened_at',
 'notify',
'made_sla',
 'location',
 'reopened_by',
 'reopened_time',
 'knowledge',
 'u_incident_id',
'u_watch_list_it',
 'u_hypercare_related',
 'u_group_visibility',
 'group_list',
 'follow_up',
 'u_external_reference',
 'expected_start',
'calendar_duration',
 'due_date',
 'sys_domain',
 'u_description_html',
 'description',
 'delivery_task',
 'delivery_plan',
 'sys_created_by',
 'correlation_display',
 'contact_type',
 'u_confirm_priority_1',
 'cmdb_ci',
'u_comment_added_it',
 'u_comment_added',
 'closed_by',
'close_notes',
 'close_code',
 'rfc',
 'caused_by',
 'business_service',
 'business_stc',
 'business_duration',
 'approval_set',
 'approval_history',
 'approval',
 'additional_assignee_list',
 'comments',
 'work_start',
 'work_end',
 'activity_due',
 'caller_id',
 'assignment_group',
 'assigned_to',
 'assigned_to.email',
 'active',
'caller_id.company',
'caller_id.country',
 'caller_id.department',
 'caller_id.sys_domain',
 'caller_id.location',
 'company.country',
 'company.u_location.full_name',
 'company.u_location.time_zone',
 'company.rank_tier',
 'company.primary',
 'Unnamed: 140']

In [49]:
data = data.drop(remove_list, axis=1)

In [52]:
data.head()

urgency u_major_incident   impact escalation       sys_created_on company  \
0  3 - Low            FALSE  3 - Low     Normal  06-06-2011 23:07:16     201   
1  3 - Low            FALSE  3 - Low     Normal  07-06-2011 17:07:28     201   
2  3 - Low            FALSE  3 - Low     Normal  13-06-2011 16:59:18     215   
3  3 - Low            FALSE  3 - Low     Normal  14-06-2011 14:36:03     215   
4  3 - Low            FALSE  3 - Low     Normal  14-06-2011 15:35:51     201   

             closed_at category      priority  \
0  07-07-2011 06:00:05  Failure  5 - Planning   
1  09-08-2011 06:00:10  Service  5 - Planning   
2  20-06-2011 06:00:00  Failure  5 - Planning   
3  15-08-2011 06:00:09  Failure  5 - Planning   
4  13-07-2011 06:00:06  Failure  5 - Planning   

  caller_id.u_communication_language company.u_location.country  \
0                                 DE                Switzerland   
1                                 DE                Switzerland   
2                                 EN                Switzerland   
3                                 EN                Switzerland   
4                                 DE                Switzerland   

  company.u_location.zip  
0                   8606  
1                   8606  
2                   8606  
3                   8606  
4                   8606

In [58]:
#Removing lettering from what is supposed tobe a numerical value
ind_val=[]
num_col = ["urgency", "impact", "priority"]
for col in (num_col):
    print(col)
    for i in range(len(data)):
        val = data.iloc[i][col]
        if isinstance(val, int):
            data.set_value([i], col, val)
            continue
        try: 
            val = val.split()[0]
        if isinstance(val, str):
            print("String where there shouldn be at index", i)
            ind_val += [i]
            continue
        data.set_value([i], col, val)
    print("Finito with " + col)
print("Finito total")

#Turning string type booleans into bool type booleans
ind_val=[]
for i in range(len(data)):
    val = data.iloc[i]["u_major_incident"]
    if val == "FALSE":
        data.set_value([i], "u_major_incident", False)
    elif val == "TRUE":
        data.set_value([i], "u_major_incident", True)
    else:
        ind_val += [i]
len(ind_val)
#Removing or changing erroneus entries


urgency


/home/marius/.local/lib/python3.6/site-packages/ipykernel_launcher.py:9: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  if __name__ == '__main__':
/home/marius/.local/lib/python3.6/site-packages/ipykernel_launcher.py:15: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
  from ipykernel import kernelapp as app


String where there shouldn be at index 8679
String where there shouldn be at index 8680
String where there shouldn be at index 8681
String where there shouldn be at index 8682
String where there shouldn be at index 8683
String where there shouldn be at index 8684
String where there shouldn be at index 8685
String where there shouldn be at index 8686
String where there shouldn be at index 8687
String where there shouldn be at index 8688
String where there shouldn be at index 8689
String where there shouldn be at index 8690
String where there shouldn be at index 8691
String where there shouldn be at index 8692
String where there shouldn be at index 8693
String where there shouldn be at index 8694
String where there shouldn be at index 8695
String where there shouldn be at index 8696
String where there shouldn be at index 8697
String where there shouldn be at index 8698
String where there shouldn be at index 8699
String where there shouldn be at index 8700
String where there shouldn be at

String where there shouldn be at index 9403
String where there shouldn be at index 9404
String where there shouldn be at index 9405
String where there shouldn be at index 9406
String where there shouldn be at index 9407
String where there shouldn be at index 9408
String where there shouldn be at index 9409
String where there shouldn be at index 9410
String where there shouldn be at index 9411
String where there shouldn be at index 9412
String where there shouldn be at index 9413
String where there shouldn be at index 9414
String where there shouldn be at index 9415
String where there shouldn be at index 9416
String where there shouldn be at index 9417
String where there shouldn be at index 9418
String where there shouldn be at index 9419
String where there shouldn be at index 9420
String where there shouldn be at index 9421
String where there shouldn be at index 9422
String where there shouldn be at index 9423
String where there shouldn be at index 9424
String where there shouldn be at

String where there shouldn be at index 10055
String where there shouldn be at index 10056
String where there shouldn be at index 10057
String where there shouldn be at index 10058
String where there shouldn be at index 10059
String where there shouldn be at index 10060
String where there shouldn be at index 10061
String where there shouldn be at index 10062
String where there shouldn be at index 10063
String where there shouldn be at index 10064
String where there shouldn be at index 10065
String where there shouldn be at index 10066
String where there shouldn be at index 10067
String where there shouldn be at index 10068
String where there shouldn be at index 10069
String where there shouldn be at index 10070
String where there shouldn be at index 10071
String where there shouldn be at index 10072
String where there shouldn be at index 10073
String where there shouldn be at index 10074
String where there shouldn be at index 10075
String where there shouldn be at index 10076
String whe

...

String where there shouldn be at index 32047
String where there shouldn be at index 32048
String where there shouldn be at index 32049
String where there shouldn be at index 32050
String where there shouldn be at index 32051
String where there shouldn be at index 32052
String where there shouldn be at index 32053
String where there shouldn be at index 32054
String where there shouldn be at index 32055
String where there shouldn be at index 32056
String where there shouldn be at index 32057
String where there shouldn be at index 32058
String where there shouldn be at index 32059
String where there shouldn be at index 32060
String where there shouldn be at index 32061
String where there shouldn be at index 32062
String where there shouldn be at index 32063
String where there shouldn be at index 32064
String where there shouldn be at index 32065
String where there shouldn be at index 32066
String where there shouldn be at index 32067
String where there shouldn be at index 32068
String whe

String where there shouldn be at index 32796
String where there shouldn be at index 32797
String where there shouldn be at index 32798
String where there shouldn be at index 32799
String where there shouldn be at index 32800
String where there shouldn be at index 32801
String where there shouldn be at index 32802
String where there shouldn be at index 32803
String where there shouldn be at index 32804
String where there shouldn be at index 32805
String where there shouldn be at index 32806
String where there shouldn be at index 32807
String where there shouldn be at index 32808
String where there shouldn be at index 32809
String where there shouldn be at index 32810
String where there shouldn be at index 32811
String where there shouldn be at index 32812
String where there shouldn be at index 32813
String where there shouldn be at index 32814
String where there shouldn be at index 32815
String where there shouldn be at index 32816
String where there shouldn be at index 32817
String whe

String where there shouldn be at index 33546
String where there shouldn be at index 33547
String where there shouldn be at index 33548
String where there shouldn be at index 33549
String where there shouldn be at index 33550
String where there shouldn be at index 33551
String where there shouldn be at index 33552
String where there shouldn be at index 33553
String where there shouldn be at index 33554
String where there shouldn be at index 33555
String where there shouldn be at index 33556
String where there shouldn be at index 33557
String where there shouldn be at index 33558
String where there shouldn be at index 33559
String where there shouldn be at index 33560
String where there shouldn be at index 33561
String where there shouldn be at index 33562
String where there shouldn be at index 33563
String where there shouldn be at index 33564
String where there shouldn be at index 33565
String where there shouldn be at index 33566
String where there shouldn be at index 33567
String whe

/home/marius/.local/lib/python3.6/site-packages/ipykernel_launcher.py:24: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead
/home/marius/.local/lib/python3.6/site-packages/ipykernel_launcher.py:26: FutureWarning: set_value is deprecated and will be removed in a future release. Please use .at[] or .iat[] accessors instead


KeyboardInterrupt: 

In [ ]:
#Removing columns with non-categorical text entries

In [ ]:
#Remove nan rows for comapany country, location, and location full name

def string_nan_remover(column_list):
    ind_val = []
    for col in column_list:
        #Removing nan rows for solution category. They are often flagged as pending.
    
        for i in range(len(data)):
            val = data.iloc[i][col]
            if not isinstance(val, str):
                ind_val += [i]
                print("NaN at index", i)
    ind_val = list(set(ind_val))
    data = data.drop(ind_val)


In [ ]:
#Calculating time spent on ticket, adding new column, and dropping old ones

def date_func(datestring):
    FMT = '%d-%m-%Y %H:%M:%S'
    t1 = datetime.strptime(datestring, FMT)
    return t1

#Creating new column with time spent to complete ticket
lis = ['sys_created_on', 'closed_at']
for col in lis:
    data[col] = data[col].map(lambda col: date_func(col))

data["Completion Time"] = data['closed_at'] - data['sys_created_on'] 
data["Completion Time"] = data["Completion Time"].map(lambda col: float(col.total_seconds()/3600))
data = data.drop(lis)

## Preliminary analysis

In [ ]:
#Looking at correlations

## Building decision tree

## Building simple Neural net

## Visualizing results and comparing